In [1]:
import os

In [2]:
os.environ['PROJ_LIB'] = '/Users/patricksaul/anaconda3/share/proj'

In [3]:
import plotly.express as px
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
from mpl_toolkits.basemap import Basemap
import datetime as dt

In [4]:
import io
import requests

# Import People Groups Base File

In [9]:
#Data set for all people groups
url = "https://joshuaproject.net/resources/datasets/1"
response = requests.get(url)

SSLError: HTTPSConnectionPool(host='joshuaproject.net', port=443): Max retries exceeded with url: /resources/datasets/1 (Caused by SSLError(SSLError("bad handshake: SysCallError(54, 'ECONNRESET')")))

In [6]:
todayFileName = 'AllPeoplesByCountry_' + str(dt.datetime.today().date()) + '.csv'

In [7]:
open(todayFileName,'wb').write(response.content)

NameError: name 'response' is not defined

In [ ]:
#pg_df = pd.read_csv(todayFileName, low_memory=False,skiprows=1)

In [10]:

pg_df = pd.read_csv('AllPeoplesByCountry_2020-07-25.csv', low_memory=False,skiprows=1)

All Columns: ROG, Ctry, PeopleID3, ROP3, PeopNameAcrossCountries, PeopNameInCountry, Population, JPScale, LeastReached, ROL3, PrimaryLanguageName, BibleStatus, RLG3, PrimaryReligion, PercentAdherents, PercentEvangelical, PeopleID1, ROP1, AffinityBloc, PeopleID2, ROP2, PeopleCluster, CountOfCountries, RegionCode, RegionName, ROG2, Continent, 10_40Window, IndigenousCode, WorkersNeeded, Frontier, Latitude, Longitude

In [ ]:
pg_df.head()

In [ ]:
pg_df.describe()

# Track Changes Over Time (WIP)

In [14]:
olddt = '2020-06-29'
#newdt = str(dt.datetime.today().date())
newdt = '2020-07-25'

In [15]:
old_df = pd.read_csv('AllPeoplesByCountry_' + olddt + '.csv', low_memory=False,skiprows=1)
new_df = pd.read_csv('AllPeoplesByCountry_' + newdt + '.csv', low_memory=False,skiprows=1)

In [16]:
old_df['Snapshot Date'] = olddt

In [17]:
new_df['Snapshot Date'] = newdt

In [18]:
#Concatenate old and new
full_df = pd.concat([old_df,new_df])

In [19]:
change_df = full_df.drop_duplicates(keep='last')

In [20]:
full_df = pd.concat([old_df,change_df])

In [21]:
full_df['ID'] = full_df['PeopleID3'].astype(str).str.cat(full_df['Ctry'], sep=' ')

In [22]:
full_df = full_df.sort_values(by=['ID'])

In [23]:
full_df.head()

ROG3              Ctry  PeopleID3      ROP3 PeopNameAcrossCountries  \
12427   PP  Papua New Guinea    10119.0  100004.0                   Abaga   
12427   PP  Papua New Guinea    10119.0  100004.0                   Abaga   
12744   PP  Papua New Guinea    10119.0  100004.0                   Abaga   
9694    MY          Malaysia    10120.0  100005.0             Abai Sungai   
9694    MY          Malaysia    10120.0  100005.0             Abai Sungai   

      PeopNameInCountry  Population  JPScale LeastReached ROL3  ... ROG2  \
12427             Abaga       200.0      5.0            N  abg  ...  AUS   
12427             Abaga       200.0      5.0            N  abg  ...  AUS   
12744             Abaga       200.0      5.0            N  abg  ...  AUS   
9694        Abai Sungai      1500.0      1.0            Y  abf  ...  ASI   
9694        Abai Sungai      1500.0      1.0            Y  abf  ...  ASI   

       Continent  10_40Window IndigenousCode  WorkersNeeded  Frontier  \
12427  Australia            N              Y            NaN         N   
12427  Australia            N              Y            NaN         N   
12744  Australia            N              Y            NaN         N   
9694        Asia            Y              Y            1.0         Y   
9694        Asia            Y              Y            1.0         Y   

       Latitude  Longitude Snapshot Date                        ID  
12427  -6.11863  145.66645    2020-06-29  10119.0 Papua New Guinea  
12427  -6.11863  145.66645    2020-06-29  10119.0 Papua New Guinea  
12744  -6.11863  145.66645    2020-07-25  10119.0 Papua New Guinea  
9694    5.68353  118.37470    2020-06-29          10120.0 Malaysia  
9694    5.68353  118.37470    2020-06-29          10120.0 Malaysia  

[5 rows x 35 columns]

In [24]:
# Method below highly inefficient so commented out, but descriptive of the logic we are executing with the NumPy Where
#function below
# ##Iterate through to calculate change
# def changeCalc(df, calcField, outField):
#     prevIdx = None
#     currLoc = 0
#     for index, row in df.iterrows():
#         #If previous row and current row are the same
#         if prevIdx == index:
#             #Subtract the current row's calcField from the previous row's calcField and store in the df at
#             #current integer based position
#             df.iloc[:,(currLoc,outField)] = row[calcField] - df.iloc[:,(currLoc - 1,calcField)]
#         prevIdx = index
#         currLoc +=1

        
# full_df = changeCalc(full_df, 'PercentEvangelical', 'PercEvChg')

full_df['PercEvChg'] = np.where(full_df['ID'].shift(1) == full_df['ID'], full_df['PercentEvangelical'] - \
                               full_df.shift(1)['PercentEvangelical'],np.NaN)

In [25]:
full_df[(full_df['PercEvChg'] != 0) & (~pd.isna(full_df['PercEvChg']))]

ROG3        Ctry  PeopleID3      ROP3    PeopNameAcrossCountries  \
11539   NI     Nigeria    10191.0  100135.0                       Ahan   
9221    KZ  Kazakhstan    10256.0  100235.0                      Altai   
9024    KZ  Kazakhstan    10256.0  100235.0                      Altai   
13674   PE        Peru    10268.0  100255.0      Amarakaire, Harakmbet   
3320    CO    Colombia    10313.0  100332.0                    Andoque   
3268    CO    Colombia    10313.0  100332.0                    Andoque   
343     AS   Australia    10330.0  100358.0               Anglo-Romani   
87      AG     Algeria    10379.0  100226.0  Algerian, Arabic-speaking   
88      AG     Algeria    10379.0  100226.0  Algerian, Arabic-speaking   
13682   PE        Peru    10452.0  100554.0          Asheninka, Pichis   
13365   PE        Peru    10452.0  100554.0          Asheninka, Pichis   
11334   NI     Nigeria    10467.0  100578.0                        Asu   
15884   TO        Togo    10560.0  100753.0                Koussountou   
4901    GH       Ghana    10637.0  100952.0                      Ligbi   
8099    ID   Indonesia    10658.0  101002.0                     Banjar   
7906    ID   Indonesia    10658.0  101002.0                     Banjar   
11584   NI     Nigeria    10702.0  101095.0                     Bashar   
9275    KG  Kyrgyzstan    10705.0  101100.0                    Bashkir   
3348    CO    Colombia    10733.0  101147.0               Embera-Baudo   
4911    GH       Ghana    10734.0  101148.0                      Baule   
11602   NI     Nigeria    10907.0  101551.0              Boko, Bokonya   
2580    CD        Chad    10929.0  101586.0                   Bon Gula   
11473   NI     Nigeria    10949.0  101622.0           Fulani, Nigerian   
1801    CB    Cambodia    10960.0  101655.0                       Brao   
10626   MG    Mongolia    11037.0  101792.0           Buriat, Mongolia   
10419   MG    Mongolia    11037.0  101792.0           Buriat, Mongolia   
15546   TI  Tajikistan    11065.0  101833.0                 Belarusian   
15217   TI  Tajikistan    11065.0  101833.0                 Belarusian   
13691   PE        Peru    11095.0  101882.0                   Caquinte   
13709   PE        Peru    11105.0  101892.0                  Kakataibo   
...    ...         ...        ...       ...                        ...   
3001    CH       China    18603.0  106758.0      Mongolian, Peripheral   
3056    CH       China    18605.0  114225.0             Mongol, Khalka   
10641   MG    Mongolia    18605.0  114225.0             Mongol, Khalka   
10434   MG    Mongolia    18605.0  114225.0             Mongol, Khalka   
3058    CH       China    18607.0  114227.0            Mongol, Sichuan   
3005    CH       China    18607.0  114227.0            Mongol, Sichuan   
8832    IR        Iran    18859.0  100677.0    Azerbaijani, Azeri Turk   
11803   NI     Nigeria    18868.0  114738.0                       Ukwa   
11832   NI     Nigeria    18949.0  115516.0                       Kofa   
1875    CB    Cambodia    18987.0  115223.0                        Mel   
1864    CB    Cambodia    18993.0  115793.0                  Khmer Keh   
1545    BR      Brazil    19141.0  115357.0                  Pitaguari   
1672    BR      Brazil    19149.0  115360.0              Xukuru-Kariri   
15835   TH    Thailand    19258.0  115533.0               Thai, Khorat   
11552   NI     Nigeria    19304.0  115037.0                       Anca   
11918   NI     Nigeria    19306.0  115377.0                     Ndunda   
11812   NI     Nigeria    19556.0  115586.0           Kaningkom-Nindem   
13366   PE        Peru    19568.0  115242.0   Asheninka, South Ucayali   
1503    BR      Brazil    20070.0  115119.0                    Karuazu   
1569    BR      Brazil    20094.0  115948.0                    Pankara   
1585    BR      Brazil    20100.0  115636.0                     Pipipa   
1543    BR      Brazil    20100.0  115636.0                     Pipipa   
3384    CO

# Map Visualization Prep

In [26]:
ur_df_plot = full_df

In [27]:
ur_df_plot = ur_df_plot.drop_duplicates(keep='last')

In [28]:
ur_df_plot = ur_df_plot[~pd.isna(ur_df_plot['Population'])]

In [29]:
ur_df_plot = ur_df_plot[ur_df_plot['LeastReached'] == 'Y']

In [30]:
lat = ur_df_plot['Latitude'].values
lon = ur_df_plot['Longitude'].values

In [31]:
ur_df_plot.head()

ROG3      Ctry  PeopleID3      ROP3 PeopNameAcrossCountries  \
9694   MY  Malaysia    10120.0  100005.0             Abai Sungai   
9694   MY  Malaysia    10120.0  100005.0             Abai Sungai   
9896   MY  Malaysia    10120.0  100005.0             Abai Sungai   
4126   EG     Egypt    10125.0  100011.0                   Abaza   
4126   EG     Egypt    10125.0  100011.0                   Abaza   

     PeopNameInCountry  Population  JPScale LeastReached ROL3  ... Continent  \
9694       Abai Sungai      1500.0      1.0            Y  abf  ...      Asia   
9694       Abai Sungai      1500.0      1.0            Y  abf  ...      Asia   
9896       Abai Sungai      1500.0      1.0            Y  abf  ...      Asia   
4126   Abaza, Arabized     14000.0      1.0            Y  arz  ...    Africa   
4126   Abaza, Arabized     14000.0      1.0            Y  arz  ...    Africa   

      10_40Window  IndigenousCode WorkersNeeded  Frontier   Latitude  \
9694            Y               Y           1.0         Y   5.683530   
9694            Y               Y           1.0         Y   5.683530   
9896            Y               Y           1.0         Y   5.683530   
4126            Y               Y           1.0         Y  30.492752   
4126            Y               Y           1.0         Y  30.492752   

       Longitude Snapshot Date                ID  PercEvChg  
9694  118.374700    2020-06-29  10120.0 Malaysia        NaN  
9694  118.374700    2020-06-29  10120.0 Malaysia        0.0  
9896  118.374700    2020-07-25  10120.0 Malaysia        0.0  
4126   31.567505    2020-06-29     10125.0 Egypt        NaN  
4126   31.567505    2020-06-29     10125.0 Egypt        0.0  

[5 rows x 36 columns]

## Plotly (Interactive)

In [32]:
#From https://plotly.com/python/scatter-plots-on-maps/
#Size by population, color by # evangelical

px.set_mapbox_access_token(open('mapbox_token.txt').read())
fig1 = px.scatter_mapbox(ur_df_plot, lat="Latitude",
                     lon = "Longitude",
                     color="PercentEvangelical", # which column to use to set the color of markers
                     hover_name="PeopNameInCountry", # column added to hover information
                     size="Population", # size of markers
                     color_continuous_scale=px.colors.sequential.YlOrRd_r,
                     zoom=0.5)
# fig.update_layout(mapbox_style="open-street-map")
fig1.show()

In [35]:
#From https://plotly.com/python/scatter-plots-on-maps/
#Size by population, color by % change evangelical
#Need to fix visual

chgPlot = ur_df_plot.loc[ur_df_plot['PercEvChg'] != 0]
chgPlot = chgPlot[~pd.isna(chgPlot['PercEvChg'])]

px.set_mapbox_access_token(open('mapbox_token.txt').read())
fig2 = px.scatter_mapbox(chgPlot, lat="Latitude",
                     lon = "Longitude",
                     color="PercEvChg", # which column to use to set the color of markers
                     hover_name="PeopNameInCountry", # column added to hover information
                     size="Population", # size of markers
                     color_continuous_scale=px.colors.sequential.Blackbody,
                     zoom=0.5)
# fig.update_layout(mapbox_style="open-street-map")
fig2.show()

In [ ]:
print(chgPlot['PercEvChg'].min())

In [ ]:
chgPlot[chgPlot['PercEvChg'] == -20]